In [3]:
import numpy as np
import pandas as pd
import causalml
import random

import plotly.io as pio
pio.templates.default = "plotly_white"

import plotly.express as px
import plotly.offline as pyo
import plotly.graph_objs as go

import pickle
import datetime

from optuna.visualization import plot_contour, plot_parallel_coordinate, plot_slice, plot_param_importances, plot_rank
#pyo.init_notebook_mode()

%matplotlib inline

random_state = 123

/Users/linafaik/.pyenv/versions/3.9.16/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning:

IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html



In [2]:
cd ..

/Users/linafaik/Documents/projects/uplift_modeling


In [3]:
from src.training import *
from src.viz import *

Failed to import duecredit due to No module named 'duecredit'


## 1. Model training

In [4]:
# target column among the following values: "visit", "conversion"
col_target = "visit"

# treatment column among the following values: "treatment", "exposure"
col_treatment = "treatment"

In [5]:
p = 0.1

cols = ['f0', 'f1', 'f10', 'f11', 'f2', 'f3', 'f4', 'f5', 'f6', 'f7', 'f8', 'f9']

train_df = pd.read_csv(
    'outputs/criteo_train.csv', usecols = cols + [col_target, col_treatment],
    skiprows=lambda i: i>0 and random.random() > p)

test_df = pd.read_csv(
    'outputs/criteo_test.csv', usecols = cols + [col_target, col_treatment],
    skiprows=lambda i: i>0 and random.random() > p)

train_df['treatment_group'] = train_df[col_treatment].replace({0:'control', 1:'treatment'})
test_df['treatment_group'] = test_df[col_treatment].replace({0:'control', 1:'treatment'})

print('train', train_df.shape)
print('test', test_df.shape)

train_df.head()

train (978439, 15)
test (209500, 15)


f0        f1        f2        f3        f4        f5        f6  \
0  1.099174 -0.098397 -0.775800  0.374792 -0.169941  0.201578  0.626275   
1  0.782907 -0.098397  1.495522  0.374792 -0.169941  0.201578 -1.982847   
2 -0.975298 -0.098397 -0.775800 -1.600195 -0.169941  0.201578 -1.560547   
3 -1.302568 -0.098397  1.259660  0.374792 -0.169941  0.201578  0.971965   
4 -1.302568 -0.098397 -0.116574  0.374792 -0.169941  0.201578  0.971965   

         f7        f8        f9       f10       f11  treatment  visit  \
0 -0.222262  0.675653 -0.404445 -0.196344  0.100345          1      0   
1 -0.222262 -0.401905 -0.404445 -0.196344  0.100345          0      0   
2 -0.222262  0.675653 -0.404445 -0.196344  0.100345          1      0   
3 -0.222262 -1.104595 -0.404445 -0.196344  0.100345          1      1   
4 -0.222262  0.179066  0.334946 -0.196344  0.100345          1      0   

  treatment_group  
0       treatment  
1         control  
2       treatment  
3       treatment  
4       treatment

In [6]:
from causalml.inference.tree import UpliftTreeClassifier, UpliftRandomForestClassifier

uplift_model = UpliftTreeClassifier(
    max_depth = 3, 
    min_samples_leaf = 100, 
    min_samples_treatment = 10, 
    n_reg = 100, 
    evaluationFunction='KL', 
    control_name='control',
    honesty=False
)

uplift_model = UpliftRandomForestClassifier(
    n_estimators = 10,
    max_depth = 5,
    min_samples_leaf = 10,
    min_samples_treatment = 3,
    n_reg = 10,
    normalization = True,
    evaluationFunction = "ED",
    control_name='control',
    honesty = False
)

uplift_model.fit(
    train_df[cols].values,
    treatment=train_df['treatment_group'].values,
    y=train_df[col_target].values
)

In [7]:
uplift_model.classes_

['control', 'treatment']

## 2. Model inference

In [8]:
# for UpliftTreeClassifier uplift models

# pred_df = pd.DataFrame(
    # uplift_model.predict(test_df[cols].values),
    # columns=uplift_model.classes_)

In [9]:
pred_df = uplift_model.predict(test_df[cols].values, full_output=True)[uplift_model.classes_]

In [10]:
pred_df["best_treatment_index"] = np.argmax(pred_df.values, axis=1)
pred_df["best_treatment"] = pred_df["best_treatment_index"].map(
    {i:c for i, c in enumerate(uplift_model.classes_)}
)


pred_df.head()

control  treatment  best_treatment_index best_treatment
0  0.006410   0.007276                     1      treatment
1  0.006410   0.007276                     1      treatment
2  0.006410   0.007276                     1      treatment
3  0.006410   0.007276                     1      treatment
4  0.235806   0.292953                     1      treatment

In [11]:
pred_df.groupby("best_treatment").best_treatment_index.count()/pred_df.shape[0]*100

best_treatment
control       0.3179
treatment    99.6821
Name: best_treatment_index, dtype: float64

### 2.3. Model evaluation

In [12]:
pred_df["uplift"] = pred_df.apply(
    lambda df: df[df["best_treatment"]], axis=1
)

In [13]:
from sklift.metrics import uplift_at_k, uplift_auc_score, qini_auc_score, weighted_average_uplift

# Uplift@30%
uplift_at_k_score = uplift_at_k(
    y_true=test_df[col_target], 
    uplift=pred_df["uplift"],
    treatment=test_df["treatment_group"].replace({"treatment":1,"control":0}),
    strategy='overall', k=0.3
)

uplift_at_k_score

0.028269898179273167

In [14]:
# Area Under Uplift Curve
uplift_auc = uplift_auc_score(
    y_true=test_df[col_target], 
    uplift=pred_df["uplift"],
    treatment=test_df["treatment_group"].replace({"treatment":1,"control":0}),
)
uplift_auc

0.030702458093635105

In [15]:
# Area Under Qini Curve
qini_coef = qini_auc_score(
    y_true=test_df[col_target], 
    uplift=pred_df["uplift"],
    treatment=test_df["treatment_group"].replace({"treatment":1,"control":0}),
)
qini_coef

0.07904419222072331

In [16]:
# Weighted average uplift

# It is an average of uplift by percentile.
# Weights are sizes of the treatment group by percentile.

wau = weighted_average_uplift(
    y_true=test_df[col_target], 
    uplift=pred_df["uplift"],
    treatment=test_df["treatment_group"].replace({"treatment":1,"control":0}),
)
wau

0.006950292406935091

In [17]:
# evaluate(train_df, cols, col_target, uplift_model, uplift_auc_score)

In [18]:
evaluate(test_df, cols, col_target, uplift_model, uplift_at_k, {"strategy":"overall", "k":100})

0.06631299734748008

In [19]:
plot_uplift(test_df, col_target, pred_df[["uplift"]], normalize=True)

In [20]:
from sklift.metrics import uplift_by_percentile

uplift_by_perc_df =  uplift_by_percentile(
    test_df[col_target], 
    pred_df["uplift"],
    test_df["treatment_group"].replace({"treatment":1,"control":0}),
    strategy="overall", 
    total=False, 
    std=True, 
    bins=10
)

uplift_by_perc_df

n_treatment  n_control  response_rate_treatment  \
percentile                                                    
0-10              18090       2860                 0.342289   
10-20             17887       3063                 0.086991   
20-30             17804       3146                 0.024264   
30-40             17691       3259                 0.008988   
40-50             17639       3311                 0.003288   
50-60             17757       3193                 0.002196   
60-70             17789       3161                 0.002305   
70-80             17676       3274                 0.003112   
80-90             17705       3245                 0.001864   
90-100            17874       3076                 0.001734   

            response_rate_control    uplift  std_treatment  std_control  \
percentile                                                                
0-10                     0.298252  0.044037       0.003528     0.008555   
10-20                    0.070519  0.016471       0.002107     0.004626   
20-30                    0.017165  0.007100       0.001153     0.002316   
30-40                    0.007364  0.001623       0.000710     0.001498   
40-50                    0.001510  0.001778       0.000431     0.000675   
50-60                    0.004698 -0.002501       0.000351     0.001210   
60-70                    0.001582  0.000723       0.000360     0.000707   
70-80                    0.002138  0.000974       0.000419     0.000807   
80-90                    0.001849  0.000015       0.000324     0.000754   
90-100                   0.003251 -0.001517       0.000311     0.001026   

            std_uplift  
percentile              
0-10          0.009253  
10-20         0.005083  
20-30         0.002587  
30-40         0.001657  
40-50         0.000801  
50-60         0.001260  
60-70         0.000793  
70-80         0.000909  
80-90         0.000821  
90-100        0.001073

In [21]:
data = go.Bar(
    x = uplift_by_perc_df.index,
    y = uplift_by_perc_df.uplift,
    marker_color='coral',
    error_y = dict(
        type='data', 
        array=uplift_by_perc_df.std_uplift*2,
        visible=True
    ),
    text=[f"{round(x)}%" for x in uplift_by_perc_df.uplift*100]
)

go.Figure(data, 
          layout={'width':1000, 'height':400, 'title':'Uplift per percentile', 
                  "xaxis": {"title" : "Percentile"}, "yaxis": {"title" : "Uplift (%)"}}
)

In [22]:
data = [
    go.Bar(
        x = uplift_by_perc_df.index,
        y = uplift_by_perc_df.response_rate_treatment*100,
        name= "response rate (treatment)",
        marker_color='coral',
        error_y = dict(
            type='data', 
            array=uplift_by_perc_df.std_treatment*2,
            visible=True
        ),
        text=[f"{round(x)}%" for x in uplift_by_perc_df.response_rate_treatment*100]
    ),
    go.Bar(
        x = uplift_by_perc_df.index,
        y = uplift_by_perc_df.response_rate_control*100,
        name= "response rate (control)",
         marker_color='lightgrey',
        error_y = dict(
            type='data', 
            array=uplift_by_perc_df.std_control*2,
            visible=True
        ),
        text=[f"{round(x)}%" for x in uplift_by_perc_df.response_rate_control*100]
    )
]

go.Figure(
    data, layout={'width':1000, 'height':400, 'title':'Response rates per percentile', 
                  "xaxis": {"title" : "Percentile"}, "yaxis": {"title" : "Response rate (%)"}}
)

## 3. Hyperparameter fine-tuning

### Baselines

In [23]:
from sklift.models import SoloModel
from sklearn.ensemble import RandomForestClassifier
from sklift.metrics import uplift_auc_score, uplift_at_k

sm = SoloModel(RandomForestClassifier(n_estimators=100))
sm = sm.fit(train_df[cols], train_df[col_target], train_df[col_treatment])

pred_sm = sm.predict(test_df[cols])

uplift_auc_score(
        y_true=test_df[col_target], 
        uplift=pred_sm,
        treatment=test_df["treatment_group"].replace({"treatment":1,"control":0})
    )

0.01025366419753112

In [24]:
# Uplift@30%
uplift_at_k(
    y_true=test_df[col_target], 
    uplift=pred_sm,
    treatment=test_df["treatment_group"].replace({"treatment":1,"control":0}),
    strategy='overall', k=0.3
)

0.022420485818029565

In [ ]:
uplifts_df = pd.DataFrame({
    "UpliftRandomForestClassifier": pred_df["uplift"],
    "Solo Model": pred_sm
})

fig = plot_uplift(test_df, col_target, uplifts_df, normalize = True).show()

### Uplift optimization

In [26]:
treatment_idx = np.random.choice(train_df[train_df.treatment==1].index, train_df[train_df.treatment==0].shape[0])

train_undersample_df = pd.concat([
    train_df.loc[treatment_idx],
    train_df[train_df.treatment==0]
], axis=0).reset_index(drop=True)

In [27]:
import optuna

def objective(trial, train_df, test_df, cols_features, col_treatment, 
        col_target, control_name, score_function, random_state, score_args={}):
    
    params = {
        "max_depth" : trial.suggest_int("max_depth", 3, 10),
        "min_samples_leaf": trial.suggest_int("min_samples_leaf", 10, 10),
        "n_reg": trial.suggest_discrete_uniform("n_reg", 30, 100, 10),
        "normalization": trial.suggest_categorical("normalization", [True]),
        "evaluationFunction": trial.suggest_categorical("evaluationFunction", ["KL", "Chi", "ED"]),
        "honesty":trial.suggest_categorical("honesty", [False])
    }
    
    
    uplift_model = UpliftRandomForestClassifier(
        control_name=control_name,
        random_state=random_state,
        **params
    )
    
    trial.set_user_attr(key="best_model", value=uplift_model)

    uplift_model.fit(
        train_df[cols_features].values,
        treatment=train_df[col_treatment].values,
        y=train_df[col_target].values
    )

    score_train = evaluate(
        train_df, cols_features, col_target,
        uplift_model, score_function, score_args
    )

    score_test = evaluate(
        test_df, cols_features, col_target,
        uplift_model, score_function, score_args
    )
    
    return score_test

def callback(study, trial):
    if study.best_trial.number == trial.number:
        study.set_user_attr(key="best_model", value=trial.user_attrs["best_model"])

n_trials = 50

study = optuna.create_study(
    pruner=optuna.pruners.MedianPruner(n_warmup_steps=10), 
    direction='maximize')

study.optimize(lambda trial: objective(
    trial, 
    train_df=train_df, 
    test_df=test_df,  
    cols_features=cols,
    col_treatment="treatment_group", 
    col_target=col_target,
    control_name="control",
    score_function=uplift_auc_score,
    random_state = random_state
), n_trials=n_trials, callbacks=[callback])

trial = study.best_trial
print('Score: {}'.format(trial.value))
print("Best hyperparameters: {}".format(trial.params))

best_model=study.user_attrs["best_model"]

[I 2023-12-26 17:01:21,295] A new study created in memory with name: no-name-2383e55b-cbca-47ba-b2b2-db2c0ed7c8d8
suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 17:03:07,316] Trial 0 finished with value: 0.03168672551848908 and parameters: {'max_depth': 9, 'min_samples_leaf': 10, 'n_reg': 70.0, 'normalization': True, 'evaluationFunction': 'KL', 'honesty': False}. Best is trial 0 with value: 0.03168672551848908.
suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 17:04:37,535] Trial 1 finished with value: 0.03223303190159885 and parameters: {'max_depth': 7, 'min_samples_leaf': 10, 'n_reg': 70.0, 'normalization': True, 'evaluationFunction': 'KL', 'honesty': False}. Best is

[I 2023-12-26 17:25:59,220] Trial 17 finished with value: 0.03387666816683415 and parameters: {'max_depth': 6, 'min_samples_leaf': 10, 'n_reg': 60.0, 'normalization': True, 'evaluationFunction': 'ED', 'honesty': False}. Best is trial 4 with value: 0.034556932836776216.
suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 17:27:04,890] Trial 18 finished with value: 0.031367436836915986 and parameters: {'max_depth': 4, 'min_samples_leaf': 10, 'n_reg': 50.0, 'normalization': True, 'evaluationFunction': 'Chi', 'honesty': False}. Best is trial 4 with value: 0.034556932836776216.
suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 17:28:45,208] Trial 19 finished with value: 0.033839

suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 17:51:46,350] Trial 35 finished with value: 0.034556932836776216 and parameters: {'max_depth': 6, 'min_samples_leaf': 10, 'n_reg': 30.0, 'normalization': True, 'evaluationFunction': 'ED', 'honesty': False}. Best is trial 4 with value: 0.034556932836776216.
suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 17:53:18,464] Trial 36 finished with value: 0.03248153886381352 and parameters: {'max_depth': 7, 'min_samples_leaf': 10, 'n_reg': 30.0, 'normalization': True, 'evaluationFunction': 'KL', 'honesty': False}. Best is trial 4 with value: 0.034556932836776216.
suggest_discrete_uniform has been deprecated in v3.0.0. This featur

Score: 0.034556932836776216
Best hyperparameters: {'max_depth': 6, 'min_samples_leaf': 10, 'n_reg': 30.0, 'normalization': True, 'evaluationFunction': 'ED', 'honesty': False}


In [34]:
current_timestamp = datetime.datetime.now().strftime("%Y%m%d%H")

with open(f"outputs/{current_timestamp}_baseline_single_model.pkl", "wb") as f:
    pickle.dump(sm, f)

with open(f"outputs/{current_timestamp}_uplift_model.pkl", "wb") as f:
    pickle.dump(best_model, f)
    
with open(f"outputs/{current_timestamp}_study.pkl", "wb") as f:
    pickle.dump(study, f)
    
print(current_timestamp)

2023122618


In [26]:
current_timestamp = "2023122618"

with open(f"outputs/{current_timestamp}_uplift_model.pkl", "rb") as f:
    best_model = pickle.load(f)
    
with open(f"outputs/{current_timestamp}_study.pkl", "rb") as f:
    study = pickle.load(f)

In [27]:
params = ["max_depth", "n_reg", "evaluationFunction"]
plot_parallel_coordinate(study, params=params)

In [28]:
plot_contour(study, params=params)

In [29]:
plot_slice(study, params=params)

In [30]:
plot_param_importances(study, params=params)

In [31]:
plot_rank(study, params=params)

plot_rank is experimental (supported from v3.2.0). The interface can change in the future.


In [32]:
pred_df = best_model.predict(test_df[cols].values, full_output=True)[uplift_model.classes_]
pred_df["best_treatment_index"] = np.argmax(pred_df.values, axis=1)
pred_df["best_treatment"] = pred_df["best_treatment_index"].map(
    {i:c for i, c in enumerate(uplift_model.classes_)}
)
pred_df["uplift"] = pred_df.apply(
    lambda df: df[df["best_treatment"]], axis=1
)

uplifts_df = pd.DataFrame({
    "UpliftRF (uplift)": pred_df["uplift"],
    "Solo Model": pred_sm
})

uplift_at_k(
    y_true=test_df[col_target], 
    uplift=pred_df["uplift"],
    treatment=test_df["treatment_group"].replace({"treatment":1,"control":0}),
    strategy='overall', k=0.3
)

0.0277101694433365

In [33]:
plot_uplift(test_df, col_target, uplifts_df, normalize = True)

### Uplift@30% optimization

In [35]:
import optuna

n_trials = 50

study = optuna.create_study(
    pruner=optuna.pruners.MedianPruner(n_warmup_steps=10), 
    direction='maximize')

study.optimize(lambda trial: objective(
    trial, 
    train_df=train_undersample_df, 
    test_df=test_df,  
    cols_features=cols,
    col_treatment="treatment_group", 
    col_target=col_target,
    control_name="control",
    score_function=uplift_at_k,
    score_args={"strategy": "overall", "k":0.3},
    random_state=random_state
), n_trials=n_trials, callbacks=[callback])

trial = study.best_trial
print('Score: {}'.format(trial.value))
print("Best hyperparameters: {}".format(trial.params))

best_model=study.user_attrs["best_model"]

[I 2023-12-26 18:28:01,198] A new study created in memory with name: no-name-1b5526dc-6f32-4ea4-bdd7-3eff8f871f8e
suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 18:28:33,168] Trial 0 finished with value: 0.028957633257972154 and parameters: {'max_depth': 6, 'min_samples_leaf': 10, 'n_reg': 70.0, 'normalization': True, 'evaluationFunction': 'KL', 'honesty': False}. Best is trial 0 with value: 0.028957633257972154.
suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 18:29:27,535] Trial 1 finished with value: 0.029138531332228323 and parameters: {'max_depth': 10, 'min_samples_leaf': 10, 'n_reg': 30.0, 'normalization': True, 'evaluationFunction': 'KL', 'honesty': False}. Bes

[I 2023-12-26 18:46:04,561] Trial 17 finished with value: 0.028952437456358296 and parameters: {'max_depth': 5, 'min_samples_leaf': 10, 'n_reg': 80.0, 'normalization': True, 'evaluationFunction': 'KL', 'honesty': False}. Best is trial 8 with value: 0.02930122206995016.
suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 20:02:32,724] Trial 18 finished with value: 0.028581986275945104 and parameters: {'max_depth': 9, 'min_samples_leaf': 10, 'n_reg': 60.0, 'normalization': True, 'evaluationFunction': 'Chi', 'honesty': False}. Best is trial 8 with value: 0.02930122206995016.
suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 20:03:25,963] Trial 19 finished with value: 0.0279056

suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 21:09:23,025] Trial 35 finished with value: 0.028920446094980817 and parameters: {'max_depth': 6, 'min_samples_leaf': 10, 'n_reg': 100.0, 'normalization': True, 'evaluationFunction': 'KL', 'honesty': False}. Best is trial 8 with value: 0.02930122206995016.
suggest_discrete_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., step=...) instead.
[I 2023-12-26 21:10:25,034] Trial 36 finished with value: 0.02930122206995016 and parameters: {'max_depth': 7, 'min_samples_leaf': 10, 'n_reg': 90.0, 'normalization': True, 'evaluationFunction': 'KL', 'honesty': False}. Best is trial 8 with value: 0.02930122206995016.
suggest_discrete_uniform has been deprecated in v3.0.0. This feature

Score: 0.02930122206995016
Best hyperparameters: {'max_depth': 7, 'min_samples_leaf': 10, 'n_reg': 90.0, 'normalization': True, 'evaluationFunction': 'KL', 'honesty': False}


In [41]:
current_timestamp = datetime.datetime.now().strftime("%Y%m%d%H")

with open(f"outputs/{current_timestamp}_baseline_single_model.pkl", "wb") as f:
    pickle.dump(sm, f)

with open(f"outputs/{current_timestamp}_uplift_model.pkl", "wb") as f:
    pickle.dump(best_model, f)
    
with open(f"outputs/{current_timestamp}_study.pkl", "wb") as f:
    pickle.dump(study, f)
    
print(current_timestamp)

2023122621


In [34]:
current_timestamp = "2023122621"

with open(f"outputs/{current_timestamp}_uplift_model.pkl", "rb") as f:
    best_model = pickle.load(f)
    
with open(f"outputs/{current_timestamp}_study.pkl", "rb") as f:
    study = pickle.load(f)

In [35]:
params = ["max_depth", "n_reg", "evaluationFunction"]
plot_parallel_coordinate(study, params=params)

In [36]:
plot_contour(study, params=params)

In [37]:
plot_slice(study, params=params)

In [38]:
plot_param_importances(study, params=params)

In [39]:
plot_rank(study, params=params)

plot_rank is experimental (supported from v3.2.0). The interface can change in the future.


In [40]:
pred_df = best_model.predict(test_df[cols].values, full_output=True)[uplift_model.classes_]
pred_df["best_treatment_index"] = np.argmax(pred_df.values, axis=1)
pred_df["best_treatment"] = pred_df["best_treatment_index"].map(
    {i:c for i, c in enumerate(uplift_model.classes_)}
)
pred_df["uplift"] = pred_df.apply(
    lambda df: df[df["best_treatment"]], axis=1
)

uplift_at_k(
    y_true=test_df[col_target], 
    uplift=pred_df["uplift"],
    treatment=test_df["treatment_group"].replace({"treatment":1,"control":0}),
    strategy='overall', k=0.3
)

0.02795354599023439

In [41]:
uplifts_df["UpliftRF (uplift@30%)"] = pred_df["uplift"]
plot_uplift(test_df, col_target, uplifts_df, normalize = True).show()